### Optimization Workflow EEM-25
##### Optimizing Heat Pump Systems under Dynamic Electricity Pricing: Sizing Tool and Market Mechanism Analysis

##### Done in Python 3.10.12
##### Requires following packages
##### May also work on other package versions. (Not tested)
- pandas == 2.2.1
- numpy == 1.26.4
- pyomo == 6.7.1

##### As this script utilizes CPLEX as optimizer. Ensure your machine has CPLEX installed
##### IBM ILOG CPLEX Optimization Studio 22.1.1 
##### https://www.ibm.com/support/pages/downloading-ibm-ilog-cplex-optimization-studio-2211
##### Other linear optimizer may work. (Not tested)
  

In [57]:
import pyomo.environ as pyo
from pyomo.opt import SolverFactory
from pyomo.opt.results.solver import check_optimal_termination
import pyomo.gdp as gdp
import numpy as np
import logging
import pandas as pd

In [66]:
day_ahead = pd.read_csv('DA_Prices_Germany_2023_UTC.csv', index_col=0)
air_temp = pd.read_csv('Air_Temp_2m_Fuehlsbuettel_2023.csv', index_col=0)

In [50]:
inlet_temp = -1.167*air_temp.values.ravel()+ 43.33
hp_eff = 10*air_temp.values.ravel()+350
heat_demand = -0.33*air_temp.values.ravel()+6.66
# Negative heating demand values. Does not make any sense otherwise
heat_demand[heat_demand<0] = 0

df_data = pd.concat([day_ahead.reset_index(drop=True), pd.DataFrame.from_records([inlet_temp, hp_eff, heat_demand]).T], axis=1)
df_data.columns = ['day_ahead','inlet','hp_eff','heat_demand']
# Slightly change the "dates" to simplify the time shift due to timezone !
df_data.index = pd.date_range(start='01-01-2023',periods=8760, freq='h')

# Simple Optimization Model


In [51]:
# Reserve a dictionary to analyze multiple results
dict_res = {}

In [52]:
storage_size = 20
hp_size = 10

# Apply constant linear losses depending on the storage size
storage_losses = 0.1 + (storage_size - 20)* 0.02/ 20 

# Concrete Pyomo model
energy_system = pyo.ConcreteModel()
# Generate a set of 25 hours
# -1 to 24 --> -1 is to connect the different days with each other
energy_system.time = pyo.Set(initialize=list(range(-1,24,1)),ordered=True)

# Parameter initialization with mutable parameters
# Changeable for the different days
energy_system.day_ahead_price = pyo.Param(energy_system.time, initialize=0.0, within=pyo.Reals, mutable=True)
energy_system.hp_eff = pyo.Param(energy_system.time, initialize=0.0, within=pyo.Reals, mutable=True)
energy_system.hp_size = pyo.Param(initialize=0.0, within=pyo.Reals, mutable=True)
energy_system.storage_size = pyo.Param(initialize=0.0, mutable=True, within=pyo.Reals)
energy_system.storage_losses = pyo.Param(initialize=0.0, mutable=True, within=pyo.Reals)
energy_system.storage_start = pyo.Param(initialize=0.0, mutable=True, within=pyo.Reals)
energy_system.storage_eod = pyo.Param(initialize=0.0, mutable=True, within=pyo.Reals)
energy_system.heat_demand = pyo.Param(energy_system.time, initialize=0.0, within=pyo.Reals, mutable=True)
energy_system.storage_energy_min = pyo.Param(initialize=0.0, within=pyo.Reals, mutable=True)

# Variables to be generated from the optimzer
energy_system.hp_supply = pyo.Var(energy_system.time, within=pyo.Reals)
energy_system.hp_el_demand = pyo.Var(energy_system.time, bounds=(0, hp_size/2.5), within=pyo.Reals)
energy_system.storage_energy = pyo.Var(energy_system.time, within=pyo.Reals)

# constraint containing storage energy amount
def storage_level(energy_system, i):
    # For first time step use the amount from the day before
    if i == energy_system.time.first():
        return energy_system.storage_energy[i] == energy_system.storage_start
    return (energy_system.storage_energy[i] == 
            energy_system.storage_energy[i-1] - 
            energy_system.storage_losses - 
            energy_system.heat_demand[i] + 
            energy_system.hp_supply[i])

# Limit hp supply by the electrical energy amount
def hp_supply_max(energy_system, i):
    if i == energy_system.time.first():
        return pyo.Constraint.Skip
    return (energy_system.hp_el_demand[i] <= energy_system.hp_size/2.5)    

# Ensure no negative values can occur
def hp_supply_min(energy_system, i):
    if i == energy_system.time.first():
        return pyo.Constraint.Skip
    return (energy_system.hp_supply[i] >= 0.0)    

# Connect COP (efficiency) with electrical demand and heat generation
def hp_el_demand(energy_system, i):
    if i == energy_system.time.first():
        return pyo.Constraint.Skip
    return energy_system.hp_el_demand[i] == energy_system.hp_supply[i]/ energy_system.hp_eff[i]

# Ensure the minimum energy is kept within the storage for the day
def storage_min(energy_system, i):
    if i == energy_system.time.first():
        return pyo.Constraint.Skip
    return energy_system.storage_energy[i] >= energy_system.storage_energy_min

def storage_max(energy_system,i):
    return energy_system.storage_energy[i] <= energy_system.storage_size

# Ensure storage has enough energy at end of day
def storage_eod(energy_system,i):
    if i == energy_system.time.last():
        return energy_system.storage_energy[i] >= energy_system.storage_eod
    return pyo.Constraint.Skip

def minimize_cost(energy_system):
    return sum(energy_system.day_ahead_price[i]*energy_system.hp_el_demand[i] for i in energy_system.time) 
        
energy_system.storage_level_rule = pyo.Constraint(energy_system.time, rule=storage_level)
energy_system.hp_el_demand_rule = pyo.Constraint(energy_system.time, rule=hp_el_demand)
energy_system.hp_supply_max_rule = pyo.Constraint(energy_system.time, rule=hp_supply_max)
energy_system.hp_supply_min_rule = pyo.Constraint(energy_system.time, rule=hp_supply_min)
energy_system.storage_min_rule = pyo.Constraint(energy_system.time, rule=storage_min)
energy_system.storage_max_rule = pyo.Constraint(energy_system.time, rule=storage_max)
energy_system.storage_eod_rule = pyo.Constraint(energy_system.time, rule=storage_eod)
#energy_system.negative_discharge_rule = pyo.Constraint(energy_system.time, rule=negative_discharge)
energy_system.obj = pyo.Objective(rule=minimize_cost, sense=pyo.minimize)

# Apply disjuction to ensure the minimum starting point of the heat pump
# in other words, minimum power. Otherwise it is off
energy_system.disjunction = gdp.Disjunction(energy_system.time, 
                                    rule=lambda energy_system, i: [energy_system.hp_el_demand[i]==0, 
                                                               energy_system.hp_el_demand[i]>=energy_system.hp_size/2.5/10])
# Apply bigM transformation to generate an equivalent optimization problem using bigM-relaxation
pyo.TransformationFactory('gdp.bigm').apply_to(energy_system)

# Use cplex as solver using its API
solver = SolverFactory('cplex_direct')

# List container for the daily results
res_l = []
# iterate through the different days.
for x,y in df_data.groupby(df_data.index.day_of_year):

    # Set energy loss
    energy_system.storage_losses = storage_losses
    # Set minimum storage energy to twice the maximum heat demand of the day
    energy_system.storage_energy_min = 2*y.heat_demand.max()
    # Set appropriate storage size
    energy_system.storage_size = storage_size

    # Set the storage energy at end of day 
    # Either to half of storage size
    # or minimum storage energy
    if (2*y.heat_demand.max()) >= (storage_size/2):
        energy_system.storage_eod = 2*y.heat_demand.max()
    else:
        energy_system.storage_eod = storage_size/2

    # Set hp size
    energy_system.hp_size = hp_size
    # Set "dummy" variables (index of -1) to zero 
    energy_system.hp_supply[-1] =0
    energy_system.hp_el_demand[-1]=0
    
    # Limit the heat pump supply amount
    energy_system.hp_supply.setub = hp_size

    # If x == 1 --> First day of the year
    # Assume storage is half empty
    if x == 1:
        energy_system.storage_start = storage_size/2
    # Otherwise take the value depending on the day before (result of optimization)
    else:
        energy_system.storage_start = energy_system.storage_energy.extract_values()[23]
    # Now set the paramaters based on the dataset for the day
    for i in range(len(y)):
        energy_system.hp_eff[i] = y.hp_eff.iloc[i]/100
        energy_system.day_ahead_price[i] = y.day_ahead.iloc[i]
        energy_system.heat_demand[i] = y.heat_demand.iloc[i]

    # Solve for the corresponding day
    results = solver.solve(energy_system)

    # Check whether the results are optimal
    # Means the optimization yields a results for the day 
    if check_optimal_termination(results):
        res_l += [pd.concat([pd.DataFrame.from_dict({v.name:v.extract_values() for v in energy_system.component_objects(pyo.Var,active=True)  
                                                     if v.dim() > 0 
                                                     and 
                                                     (v.name in ['hp_supply', 'hp_el_demand','heat_demand','hp_eff','day_ahead_price','storage_energy'])
                                                    }).loc[0:24],
           pd.DataFrame.from_dict({v.name:v.extract_values() for v in energy_system.component_objects(pyo.Param,active=True)  if v.dim() > 0
                                 and 
                                  (v.name in ['hp_supply', 'hp_el_demand','heat_demand','hp_eff','day_ahead_price','storage_energy'])}).loc[0:24]],axis=1)]
    else:
        break
# If the optimization can be finished for the complete year --> 365 days
# Then save the result in dict_res
if len(res_l) == 365:
    res = pd.concat(res_l).set_index(pd.date_range(start='01-01-2023',periods=8760, freq='h'))
    dict_res[(storage_size, hp_size)] = res 

In [56]:
# Calculate different KPIS 
# Due to bigM relaxation, small value (i.e. 1e-16) can occur. --> Tolerance 
# Set these values to zero.
for x,y in dict_res.items():
    for col in y.columns:
        v = y[col].values
        v[np.isclose(v, 0)] = 0
        y[col] = v

# Calculate the corresponding kpis from the configuration
# Annual electricity price and annual electricity demand
kpi = {x:[(y['hp_el_demand'] * y['day_ahead_price']).sum(),  (y['hp_el_demand']).sum()] for x,y in dict_res.items()}

# Baseline refers to values without storage --> No optimization
kpi['Baseline','Baseline'] = [sum(df_data['heat_demand'] / (df_data['hp_eff']/100) * df_data['day_ahead']),
                             sum(df_data['heat_demand'] / (df_data['hp_eff']/100))]

# Generate Dataframe from the kpis
simple_kpis = pd.DataFrame.from_dict(kpi, orient='index', columns=['Annual Electricity Price [€/a]','Annual Electricity Demand [kWh]'])
simple_kpis.index = pd.MultiIndex.from_tuples(simple_kpis.index, names=['Storage Size [kWh]','HP Size [kW_th]'])

# Export if required
# simple_kpis.to_excel('Results/KPIS.xlsx')